In [2]:
pip install atproto

  Using cached websockets-13.1-cp311-cp311-macosx_11_0_arm64.whl.metadata (6.8 kB)
Using cached websockets-13.1-cp311-cp311-macosx_11_0_arm64.whl (155 kB)
  Attempting uninstall: websockets
    Found existing installation: websockets 10.4
    Uninstalling websockets-10.4:
      Successfully uninstalled websockets-10.4
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
pyppeteer 2.0.0 requires websockets<11.0,>=10.0, but you have websockets 13.1 which is incompatible.
Note: you may need to restart the kernel to use updated packages.


In [ ]:
import os
import time
import pickle
from collections import deque
from atproto import Client
import keyring

identifier = 'elaval.bsky.social'
password = keyring.get_password('bluesky', identifier)

if not password:
    raise ValueError('No password found in keyring. Please store it first.')

# Initialize the client and log in
client = Client()

try:
    client.login(identifier, password)
    print("Login successful.")
except Exception as e:
    print(f"Login failed: {e}")

# Parameters
MAX_DEPTH = 3
TOP_N = 5
MIN_FOLLOWERS = 1000
RATE_LIMIT_DELAY = 1

# File paths
GRAPH_FILE = 'user_graph.pkl'
VISITED_FILE = 'visited_users.pkl'
QUEUE_FILE = 'user_queue.pkl'

# Load or initialize data structures
if os.path.exists(GRAPH_FILE) and os.path.exists(VISITED_FILE) and os.path.exists(QUEUE_FILE):
    with open(GRAPH_FILE, 'rb') as f:
        graph = pickle.load(f)
    with open(VISITED_FILE, 'rb') as f:
        visited = pickle.load(f)
    with open(QUEUE_FILE, 'rb') as f:
        queue = pickle.load(f)
    print("Loaded existing graph, visited set, and queue from files.")
else:
    graph = {}
    visited = set()
    queue = deque()
    print("Starting with a new graph.")

def get_profile(actor):
    """Get the profile information for a given actor (handle or DID)."""
    try:
        print(f"Fetching profile for {actor}...")
        profile = client.get_profile(actor=actor)
        print(f"Fetched profile for {actor}.")
        return profile  # Return the profile object
    except Exception as e:
        print(f"Error fetching profile for {actor}: {e}")
        return None

def get_following_handles(actor):
    """Get the list of handles the user is following."""
    following_handles = []
    cursor = None
    try:
        print(f"Fetching following list for {actor}...")
        while True:
            params = {'actor': actor}
            if cursor:
                params['cursor'] = cursor
            response = client.get_follows(**params)
            follows = response.follows
            following_handles.extend([user.handle for user in follows])
            cursor = response.cursor
            if not cursor:
                break
            print(f"Fetched {len(follows)} follows for {actor}, continuing to next page...")
            time.sleep(RATE_LIMIT_DELAY)
        print(f"Fetched total {len(following_handles)} follows for {actor}.")
        return following_handles
    except Exception as e:
        print(f"Error fetching following list for {actor}: {e}")
        return []

def build_graph():
    """Build or update the user graph."""
    total_users_processed = len(visited)
    if not queue:
        your_handle = 'elaval.bsky.social'
        initial_handles = get_following_handles(your_handle)
        your_profile = get_profile(your_handle)
        if your_profile:
            your_followers_count = your_profile.followers_count or 0
            your_avatar_url = your_profile.avatar or ''
        else:
            your_followers_count = 0
            your_avatar_url = ''
        graph[your_handle] = {
            'followers_count': your_followers_count,
            'avatar_url': your_avatar_url,
            'connections': []
        }
        for handle in initial_handles:
            queue.append((handle, 1))
        print(f"Added {len(initial_handles)} initial handles to queue.")

    total_users_in_queue = len(queue)
    print(f"Starting graph build with {total_users_in_queue} users in queue.")

    while queue:
        current_handle, depth = queue.popleft()
        total_users_in_queue = len(queue)

        if depth > MAX_DEPTH:
            continue

        if current_handle in visited:
            continue

        visited.add(current_handle)
        total_users_processed += 1

        print(f"\nProcessing {current_handle} at depth {depth}...")
        print(f"Total users processed: {total_users_processed}")
        print(f"Users remaining in queue: {total_users_in_queue}")

        # Get the profile of the current user
        current_profile = get_profile(current_handle)
        if current_profile:
            current_followers_count = current_profile.followers_count or 0
            current_avatar_url = current_profile.avatar or ''
        else:
            current_followers_count = 0
            current_avatar_url = ''

        # Initialize the current user's data in the graph
        graph[current_handle] = {
            'followers_count': current_followers_count,
            'avatar_url': current_avatar_url,
            'connections': []
        }

        # Get the users that the current user is following
        following_handles = get_following_handles(current_handle)

        # Get follower counts and filter users
        users_data = []
        for index, handle in enumerate(following_handles, start=1):
            if handle not in visited:
                profile = get_profile(handle)
                if profile:
                    followers_count = profile.followers_count or 0
                    avatar_url = profile.avatar or ''
                    if followers_count >= MIN_FOLLOWERS:
                        users_data.append({
                            'handle': handle,
                            'followers_count': followers_count,
                            'avatar_url': avatar_url
                        })
                        print(f"User {handle} has {followers_count} followers, added to consideration.")
                    else:
                        print(f"User {handle} has {followers_count} followers, below threshold.")
                    time.sleep(RATE_LIMIT_DELAY)
                else:
                    print(f"Profile not found for {handle}.")
            else:
                print(f"User {handle} already visited.")
            if index % 10 == 0:
                print(f"Processed {index} out of {len(following_handles)} follows for {current_handle}.")

        # Sort and select top N users
        top_users = sorted(users_data, key=lambda x: x['followers_count'], reverse=True)[:TOP_N]

        # Add edges to the graph
        for user in top_users:
            handle = user['handle']
            avatar_url = user['avatar_url']
            followers_count = user['followers_count']

            graph[current_handle]['connections'].append(handle)

            if handle not in graph:
                graph[handle] = {
                    'followers_count': followers_count,
                    'avatar_url': avatar_url,
                    'connections': []
                }

            queue.append((handle, depth + 1))
            print(f"Added {handle} to queue with {followers_count} followers.")

        print(f"Completed processing of {current_handle}.")

        # Save the state after processing each user
        with open(GRAPH_FILE, 'wb') as f:
            pickle.dump(graph, f)
        with open(VISITED_FILE, 'wb') as f:
            pickle.dump(visited, f)
        with open(QUEUE_FILE, 'wb') as f:
            pickle.dump(queue, f)

    print("Graph building complete.")

build_graph()


Login successful.
Loaded existing graph, visited set, and queue from files.
Starting graph build with 341 users in queue.

Processing atrupar.com at depth 2...
Total users processed: 84
Users remaining in queue: 335
Fetching profile for atrupar.com...
Fetched profile for atrupar.com.
Fetching following list for atrupar.com...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, continuing to next page...
Fetched 50 follows for atrupar.com, contin

Fetching profile for mistergeezy.bsky.social...
Fetched profile for mistergeezy.bsky.social.
User mistergeezy.bsky.social has 3078 followers, added to consideration.
Fetching profile for lebassett.bsky.social...
Fetched profile for lebassett.bsky.social.
User lebassett.bsky.social has 17988 followers, added to consideration.
Fetching profile for veggieto.bsky.social...
Fetched profile for veggieto.bsky.social.
User veggieto.bsky.social has 24918 followers, added to consideration.
Fetching profile for vincempls.bsky.social...
Fetched profile for vincempls.bsky.social.
User vincempls.bsky.social has 2802 followers, added to consideration.
Fetching profile for edroso.bsky.social...
Fetched profile for edroso.bsky.social.
User edroso.bsky.social has 10380 followers, added to consideration.
Fetching profile for arischneider.bsky.social...
Fetched profile for arischneider.bsky.social.
User arischneider.bsky.social has 4534 followers, added to consideration.
Fetching profile for lisafung.bsky

Fetching profile for markhertling.bsky.social...
Fetched profile for markhertling.bsky.social.
User markhertling.bsky.social has 61373 followers, added to consideration.
Fetching profile for general-ben.bsky.social...
Fetched profile for general-ben.bsky.social.
User general-ben.bsky.social has 22453 followers, added to consideration.
Fetching profile for intelhistorian.bsky.social...
Fetched profile for intelhistorian.bsky.social.
User intelhistorian.bsky.social has 6361 followers, added to consideration.
Fetching profile for haydencenter.bsky.social...
Fetched profile for haydencenter.bsky.social.
User haydencenter.bsky.social has 7611 followers, added to consideration.
Fetching profile for ldfreedman.bsky.social...
Fetched profile for ldfreedman.bsky.social.
User ldfreedman.bsky.social has 35887 followers, added to consideration.
Fetching profile for mirandayaver.bsky.social...
Fetched profile for mirandayaver.bsky.social.
User mirandayaver.bsky.social has 19760 followers, added to 

Fetching profile for roxanegay.bsky.social...
Fetched profile for roxanegay.bsky.social.
User roxanegay.bsky.social has 166030 followers, added to consideration.
Fetching profile for amandahoey.bsky.social...
Fetched profile for amandahoey.bsky.social.
User amandahoey.bsky.social has 5042 followers, added to consideration.
Fetching profile for jennycohn.bsky.social...
Fetched profile for jennycohn.bsky.social.
User jennycohn.bsky.social has 75546 followers, added to consideration.
Fetching profile for rachelbitecofer.bsky.social...
Fetched profile for rachelbitecofer.bsky.social.
User rachelbitecofer.bsky.social has 121459 followers, added to consideration.
Fetching profile for maryltrump.bsky.social...
Fetched profile for maryltrump.bsky.social.
User maryltrump.bsky.social has 225700 followers, added to consideration.
Fetching profile for bradleywhitford.bsky.social...
Fetched profile for bradleywhitford.bsky.social.
User bradleywhitford.bsky.social has 67995 followers, added to consi

Fetching profile for georgehahn.com...
Fetched profile for georgehahn.com.
User georgehahn.com has 99092 followers, added to consideration.
Fetching profile for manmademoon.bsky.social...
Fetched profile for manmademoon.bsky.social.
User manmademoon.bsky.social has 56649 followers, added to consideration.
Fetching profile for jerilryan.bsky.social...
Fetched profile for jerilryan.bsky.social.
User jerilryan.bsky.social has 137392 followers, added to consideration.
Fetching profile for patrickhimself.bsky.social...
Fetched profile for patrickhimself.bsky.social.
User patrickhimself.bsky.social has 5876 followers, added to consideration.
Fetching profile for mikemadrid.bsky.social...
Fetched profile for mikemadrid.bsky.social.
User mikemadrid.bsky.social has 12710 followers, added to consideration.
Fetching profile for mariainkharkiv.bsky.social...
Fetched profile for mariainkharkiv.bsky.social.
User mariainkharkiv.bsky.social has 9747 followers, added to consideration.
Fetching profile 

...

Fetching profile for beatfretz1966.bsky.social...
Fetched profile for beatfretz1966.bsky.social.
User beatfretz1966.bsky.social has 24 followers, below threshold.
Fetching profile for viranth.bsky.social...
Fetched profile for viranth.bsky.social.
User viranth.bsky.social has 13 followers, below threshold.
Fetching profile for colinmclellan.bsky.social...
Fetched profile for colinmclellan.bsky.social.
User colinmclellan.bsky.social has 10 followers, below threshold.
Fetching profile for maxbkc.bsky.social...
Fetched profile for maxbkc.bsky.social.
User maxbkc.bsky.social has 240 followers, below threshold.
Fetching profile for cko236.bsky.social...
Fetched profile for cko236.bsky.social.
User cko236.bsky.social has 91 followers, below threshold.
Fetching profile for spendersmcgee.bsky.social...
Fetched profile for spendersmcgee.bsky.social.
User spendersmcgee.bsky.social has 161 followers, below threshold.
Processed 33980 out of 36421 follows for treadres.bsky.social.
Fetching profile 

Fetching profile for rbaker45.bsky.social...
Fetched profile for rbaker45.bsky.social.
User rbaker45.bsky.social has 376 followers, below threshold.
Fetching profile for hugozumdonner.bsky.social...
Fetched profile for hugozumdonner.bsky.social.
User hugozumdonner.bsky.social has 267 followers, below threshold.
Fetching profile for zyndaquila.bsky.social...
Fetched profile for zyndaquila.bsky.social.
User zyndaquila.bsky.social has 13 followers, below threshold.
Fetching profile for hihkatharine.bsky.social...
Fetched profile for hihkatharine.bsky.social.
User hihkatharine.bsky.social has 398 followers, below threshold.
Fetching profile for lingod.bsky.social...
Fetched profile for lingod.bsky.social.
User lingod.bsky.social has 17 followers, below threshold.
Processed 34030 out of 36421 follows for treadres.bsky.social.
Fetching profile for fronsto.bsky.social...
Fetched profile for fronsto.bsky.social.
User fronsto.bsky.social has 20 followers, below threshold.
Fetching profile for j

Fetching profile for claudiahdm.bsky.social...
Fetched profile for claudiahdm.bsky.social.
User claudiahdm.bsky.social has 11 followers, below threshold.
Fetching profile for mietvinck.bsky.social...
Fetched profile for mietvinck.bsky.social.
User mietvinck.bsky.social has 32 followers, below threshold.
Fetching profile for dogcorleone.bsky.social...
Fetched profile for dogcorleone.bsky.social.
User dogcorleone.bsky.social has 179 followers, below threshold.
Fetching profile for cairos.bsky.social...
Fetched profile for cairos.bsky.social.
User cairos.bsky.social has 47 followers, below threshold.
Processed 34080 out of 36421 follows for treadres.bsky.social.
Fetching profile for nana42025.bsky.social...
Fetched profile for nana42025.bsky.social.
User nana42025.bsky.social has 23 followers, below threshold.
Fetching profile for skaswan.bsky.social...
Fetched profile for skaswan.bsky.social.
User skaswan.bsky.social has 213 followers, below threshold.
Fetching profile for kvrn.bsky.soci

Fetched profile for blueskybabs.bsky.social.
User blueskybabs.bsky.social has 2877 followers, added to consideration.
Fetching profile for donnalwentz.bsky.social...
Fetched profile for donnalwentz.bsky.social.
User donnalwentz.bsky.social has 192 followers, below threshold.
Fetching profile for ericlars2.bsky.social...
Fetched profile for ericlars2.bsky.social.
User ericlars2.bsky.social has 5645 followers, added to consideration.
Fetching profile for liberal-bastion.bsky.social...
Fetched profile for liberal-bastion.bsky.social.
User liberal-bastion.bsky.social has 7994 followers, added to consideration.
Fetching profile for steelteresa.bsky.social...
Fetched profile for steelteresa.bsky.social.
User steelteresa.bsky.social has 484 followers, below threshold.
Fetching profile for blueeyedbutch.bsky.social...
Fetched profile for blueeyedbutch.bsky.social.
User blueeyedbutch.bsky.social has 3506 followers, added to consideration.
Fetching profile for dream024.bsky.social...
Fetched pro

Fetched profile for crzyjaney.bsky.social.
User crzyjaney.bsky.social has 3279 followers, added to consideration.
Fetching profile for joywinh.bsky.social...
Fetched profile for joywinh.bsky.social.
User joywinh.bsky.social has 2437 followers, added to consideration.
Fetching profile for musicgirl1965.bsky.social...
Fetched profile for musicgirl1965.bsky.social.
User musicgirl1965.bsky.social has 1599 followers, added to consideration.
Fetching profile for porpentina2017.bsky.social...
Fetched profile for porpentina2017.bsky.social.
User porpentina2017.bsky.social has 14401 followers, added to consideration.
Fetching profile for come-on-now.bsky.social...
Fetched profile for come-on-now.bsky.social.
User come-on-now.bsky.social has 2037 followers, added to consideration.
Fetching profile for doidlemom2.bsky.social...
Fetched profile for doidlemom2.bsky.social.
User doidlemom2.bsky.social has 493 followers, below threshold.
Fetching profile for borderingorder.bsky.social...
Fetched prof